In [1]:
#https://www.machinelearningplus.com/nlp/topic-modeling-visualization-how-to-present-results-lda-models/
import json
import numpy as np, pandas as pd
import matplotlib.pyplot as plt
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import sent_tokenize, word_tokenize
sw_nltk = stopwords.words('english')
from nltk.tokenize.treebank import TreebankWordDetokenizer
#nltk.download('punkt')
from nltk.stem import WordNetLemmatizer
#nltk.download('wordnet')

import re

from matplotlib import cm
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.model_selection import (RepeatedStratifiedKFold, cross_val_score, )
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
from tomotopy import HDPModel

from lda_classification.model import TomotopyLDAVectorizer
from lda_classification.preprocess.spacy_cleaner import SpacyCleaner



#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
workers = 4 #Numbers of workers throughout the project
use_umap = False #make this True if you want to use UMAP for your visualizations
min_df = 5 #Minimum number for document frequency in the corpus
rm_top = 5 #Remove top n frequent words

In [14]:
#lem for lemmatization, stem for stemmatizing
def preprocess(data, type="lem"):
    preprocessed_data = []
    for x in data:
        #Lowerize
        x = x.lower()
        #Eliminate special characters
        x = re.sub(r'\d+', '', x)
        x = re.sub(' +', ' ', x.translate ({ord(c): "" for c in "!@#$%^&*()[]{};:,./<>?\|'`~-=_+"}).strip())
        
        #Eliminate stop words
        words = [word for word in x.split() if word not in sw_nltk] 
        x = " ".join(words)

        #Stemming / Lemmatizing
        words = word_tokenize(x)
        rootWords = []
        if type=='stem':
                ps = PorterStemmer()
                rootWords.append(ps.stem(w))
        else:
            for w in words:
                wordnet_lemmatizer = WordNetLemmatizer()
                rootWords.append(wordnet_lemmatizer.lemmatize(w))

        #x = TreebankWordDetokenizer().detokenize(rootWords)
        print(x)
        preprocessed_data.append(x.split(' '))
    return preprocessed_data
        
    #print(preprocessed_data)


#preprocess(['Hsf##123 14: . ; ,  45', 'Blu34%& 22', 'as fine as good', 'found, find, go, went', 'studies studying cries cry'])

In [15]:
# Opening JSON file
f_queries = open('Queries_Labeled.json',)
f_collection = open('collection.json')
 
# returns JSON object as
# a dictionary
data_queries = json.load(f_queries)
data_collection = json.load(f_collection)
 
# Iterating through the json
# list
#for i in data['documents']:
#    print(i)
 
queries = data_queries['documents']
collection = data_collection['TREC']['DOC']
#print(len(queries))
#print(len(collection))

# Closing file
f_queries.close()
f_collection.close()


prep_collection = []
for x in collection:
    prep_collection.append(x['text'])
prep_collection = preprocess(prep_collection)

prep_queries = []
for x in queries:
    prep_queries.append(x['text'])
prep_queries = preprocess(prep_queries)

#print(prep_queries)
#print(prep_collection)

digital computers universities part july reeves r f ca jb march pm
using synthetic images register real images surface models number image analysis tasks benefit registration image model surface imaged automatic navigation using visible light radar images requires exact alignment images digital terrain models addition automatic classification terrain using satellite imagery requires alignment deal correctly effects varying sun angle surface slope even inspection techniques certain industrial parts may improved means achieve required alignment matching real image synthetic image obtained surface model known positions light sources synthetic image intensity calculated using reflectance map convenient way describing surface reflection function surface gradient illustrate technique using landsat images digital terrain models november horn bkp bachman bl image registration synthetic images surface models automatic hill shading digital terrain models image transformation image matching shade

In [16]:
print(prep_collection)

[['digital', 'computers', 'universities', 'part', 'july', 'reeves', 'r', 'f', 'ca', 'jb', 'march', 'pm'], ['using', 'synthetic', 'images', 'register', 'real', 'images', 'surface', 'models', 'number', 'image', 'analysis', 'tasks', 'benefit', 'registration', 'image', 'model', 'surface', 'imaged', 'automatic', 'navigation', 'using', 'visible', 'light', 'radar', 'images', 'requires', 'exact', 'alignment', 'images', 'digital', 'terrain', 'models', 'addition', 'automatic', 'classification', 'terrain', 'using', 'satellite', 'imagery', 'requires', 'alignment', 'deal', 'correctly', 'effects', 'varying', 'sun', 'angle', 'surface', 'slope', 'even', 'inspection', 'techniques', 'certain', 'industrial', 'parts', 'may', 'improved', 'means', 'achieve', 'required', 'alignment', 'matching', 'real', 'image', 'synthetic', 'image', 'obtained', 'surface', 'model', 'known', 'positions', 'light', 'sources', 'synthetic', 'image', 'intensity', 'calculated', 'using', 'reflectance', 'map', 'convenient', 'way', 'd

In [22]:

# Parameters tuning using Grid Search
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

tokens_collection = []
tokens_collection.append(prep_collection)
#for x in prep_collection:
#    tokens_collection.append(np.array(word_tokenize(x)))

vectorizer = CountVectorizer(analyzer='word', min_df=10, stop_words='english', lowercase=True, token_pattern='[a-zA-Z0-9]{3,}', max_features=50000)
data_vectorized = vectorizer.fit_transform(prep_collection)

from sklearn.model_selection import GridSearchCV
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.manifold import TSNE
grid_params = {'n_components' : list(range(5,10))}
# LDA model
lda = LatentDirichletAllocation()
lda_model = GridSearchCV(lda,param_grid=grid_params)
lda_model.fit(tokens_collection)
# Estimators for LDA model
lda_model1 = lda_model.best_estimator_
print("Best LDA model's params" , lda_model.best_params_)
print("Best log likelihood Score for the LDA model",lda_model.best_score_)
print("LDA model Perplexity on train data", lda_model1.perplexity(tokens_collection))

AttributeError: 'list' object has no attribute 'lower'